In [1]:
import cartopy.crs as ccrs
import cartopy.feature as cfeature
from cartopy.mpl.gridliner import LONGITUDE_FORMATTER, LATITUDE_FORMATTER
import matplotlib.pyplot as plt
import xarray as xr

import numpy as np
import metpy
import metpy.calc as mpcalc
from metpy.plots import ctables
from metpy.cbook import get_test_data
from metpy.units import units
import os
import scipy.integrate as integrate
import datetime as dt
import glob
import json
from datetime import datetime
from datetime import timedelta
from metpy.plots import ctables
from matplotlib.colors import Normalize
from matplotlib.colors import ListedColormap, LinearSegmentedColormap, BoundaryNorm

#import wrf
import scipy
#import xcape
import xarray

In [2]:
file_dir = '/data/icond2/'
os.chdir(file_dir)

data_det_cape = xr.open_dataset('icond2_cape.nc').sel(longitude=slice(3,9,1),latitude=slice(49,51,1))
data_det_cin = xr.open_dataset('icond2_cin.nc').sel(longitude=slice(3,9,1),latitude=slice(49,51,1))
data_det_lpi = xr.open_dataset('icond2_lpi.nc').sel(longitude=slice(3,9,1),latitude=slice(49,51,1))

In [3]:
file_dir = '/data/icond2eps/'

# Changing the directory
os.chdir(file_dir)
try:
    os.remove('icond2eps_cape.nc')
    os.remove('icond2eps_cape_latlon.grib2.923a8.idx')
    os.remove('icond2eps_cin_latlon.grib2.923a8.idx')
    os.remove('icond2eps_lpi_latlon.grib2.923a8.idx')
    os.remove('icond2eps_cin.nc')
    os.remove('icond2eps_lpi.nc')
except:
    print('no file')

no file


In [4]:
data = xarray.open_dataset('icond2eps_cape_latlon.grib2', engine='cfgrib')
data.to_netcdf('icond2eps_cape.nc')
data_cape = xr.open_dataset('icond2eps_cape.nc').sel(longitude=slice(3,9,1),latitude=slice(49,51,1))

data = xarray.open_dataset('icond2eps_cin_latlon.grib2', engine='cfgrib')
data.to_netcdf('icond2eps_cin.nc')
data_cin = xr.open_dataset('icond2eps_cin.nc').sel(longitude=slice(3,9,1),latitude=slice(49,51,1))

data = xarray.open_dataset('icond2eps_lpi_latlon.grib2', engine='cfgrib')
data.to_netcdf('icond2eps_lpi.nc')
data_lpi = xr.open_dataset('icond2eps_lpi.nc').sel(longitude=slice(3,9,1),latitude=slice(49,51,1))


In [5]:
# To parse the full dataset, we can call parse_cf without an argument, and assign the returned Dataset.

data_cape = data_cape.metpy.parse_cf()
data_det_cape = data_det_cape.metpy.parse_cf()
data_cin = data_cin.metpy.parse_cf()
data_lpi = data_lpi.metpy.parse_cf()
data_det_cin = data_det_cin.metpy.parse_cf()
data_det_lpi = data_det_lpi.metpy.parse_cf()

x, y = data_lpi['LPI_MAX'].metpy.coordinates('x', 'y')

time = data_lpi['LPI_MAX'].step
member = data_lpi['LPI_MAX'].number
time2 = data_det_lpi['LPI_MAX'].metpy.time

timeinit = data_lpi.time
timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)
print(timeinit)

lpi = data_lpi['LPI_MAX']
cape = data_cape['CAPE_ML']
cin = data_cin['CIN_ML']
det_lpi = data_det_lpi['LPI_MAX']
det_cape = data_det_cape['CAPE_ML']
det_cin = data_det_cin['CIN_ML']

#rr.data = np.nan_to_num(rr.data, copy=True, nan=0)
#print(rr.data)

/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/metpy/xarray.py:349: UserWarning: More than one time coordinate present for variable "CAPE_ML".
  warnings.warn('More than one ' + axis + ' coordinate present for variable'
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/metpy/xarray.py:349: UserWarning: More than one time coordinate present for variable "CIN_ML".
  warnings.warn('More than one ' + axis + ' coordinate present for variable'
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/metpy/xarray.py:349: UserWarning: More than one time coordinate present for variable "LPI_MAX".
  warnings.warn('More than one ' + axis 

2021-07-29 09:00:00


In [6]:
def plot_background(ax):
    ax.set_extent([5, 7, 49.1, 50.5])
    ax.add_feature(cfeature.COASTLINE.with_scale('10m'), LineWidth=1)
    ax.add_feature(cfeature.BORDERS.with_scale('10m'),LineWidth=1)
    #gl = ax.gridlines(draw_labels=True,linewidth=0.5, color='gray', alpha=0.5, linestyle='--')
    #gl.xlabels_top = False
    #gl.ylabels_right = False
    #gl.xlabel_style = {'size': 12, 'color': 'black'}
    #gl.ylabel_style = {'size': 12, 'color': 'black'}
    #gl.xformatter = LONGITUDE_FORMATTER
    #gl.yformatter = LATITUDE_FORMATTER
    return ax

#import matplotlib
#cmap = matplotlib.cm.get_cmap('cubehelix_r')
#for i in range(20):
    #rgba = cmap(i)
    # rgb2hex accepts rgb or rgba
    #print(rgba)
    
cmap = ctables.colortables.get_colortable('NWSStormClearReflectivity')
newcmap = ListedColormap(cmap(np.linspace(0.25, 0.92, 28)))

cmap2 = ctables.colortables.get_colortable('NWSReflectivity')
newcmap2 = ListedColormap(cmap2(np.linspace(0.2, 0.96, 28)))

cmap4 = ctables.colortables.get_colortable('precipitation')
newcmap4 = ListedColormap(cmap4(np.linspace(0, 0.65, 14)))

colors=[(1,1,1),(0.0, 0.9254901960784314, 0.9254901960784314), 
                        (0.00392156862745098, 0.6274509803921569, 0.9647058823529412), 
                        (0.0, 0.0, 0.9647058823529412), 
                        (0.0, 1.0, 0.0), 
                        (0.0, 0.7843137254901961, 0.0), 
                        (0.0, 0.5647058823529412, 0.0), 
                        (1.0, 1.0, 0.0), 
                        (0.9058823529411765, 0.7529411764705882, 0.0), 
                        (1.0, 0.5647058823529412, 0.0), 
                        (1.0, 0.16078431372, 0.16078431372), 
                        (0.7529411764705882, 0.0, 0.0),
                        (0.59765625, 0.0, 0.0), 
                        (1.0, 0.0, 1.0), 
                        (0.6, 0.3333333333333333, 0.788235294117647),
                         (0.27,0,0.4)]
colors2 = [(1,1,1),
           (0.388235, 0.462745, 0.658824), (0.372549, 0.45098, 0.654902), (0.372549, 0.45098, 0.654902), 
           (0.356863, 0.439216, 0.65098), (0.341176, 0.427451, 0.643137), (0.32549, 0.415686, 0.639216), 
           (0.309804, 0.403922, 0.635294), (0.294118, 0.392157, 0.631373), (0.278431, 0.380392, 0.627451), 
           (0.262745, 0.368627, 0.623529), (0.262745, 0.380392, 0.635294), (0.270588, 0.407843, 0.65098), 
           (0.282353, 0.435294, 0.666667), (0.290196, 0.462745, 0.682353), (0.301961, 0.490196, 0.698039), 
           (0.309804, 0.517647, 0.713725), (0.317647, 0.545098, 0.733333), (0.329412, 0.572549, 0.74902), 
           (0.337255, 0.6, 0.764706), (0.34902, 0.623529, 0.780392), (0.356863, 0.65098, 0.796078), 
           (0.368627, 0.678431, 0.811765), (0.376471, 0.705882, 0.831373), (0.384314, 0.733333, 0.847059), 
           (0.396078, 0.760784, 0.862745), (0.403922, 0.788235, 0.878431), (0.415686, 0.815686, 0.894118),
           (0.435294, 0.839216, 0.909804), (0.407843, 0.839216, 0.843137), (0.380392, 0.839216, 0.772549), 
           (0.34902, 0.839216, 0.701961), (0.321569, 0.839216, 0.635294), (0.294118, 0.839216, 0.564706), 
           (0.262745, 0.839216, 0.494118), (0.235294, 0.839216, 0.427451), (0.207843, 0.839216, 0.356863),
           (0.066667, 0.835294, 0.094118), (0.066667, 0.819608, 0.090196), (0.062745, 0.803922, 0.090196), 
           (0.062745, 0.784314, 0.086275), (0.062745, 0.768627, 0.086275), (0.058824, 0.752941, 0.082353), 
           (0.058824, 0.737255, 0.082353), (0.058824, 0.717647, 0.078431), (0.054902, 0.701961, 0.078431), 
           (0.054902, 0.686275, 0.07451), (0.054902, 0.670588, 0.07451), (0.05098, 0.65098, 0.070588), 
           (0.05098, 0.635294, 0.070588), (0.05098, 0.619608, 0.066667), (0.047059, 0.6, 0.066667), 
           (0.047059, 0.584314, 0.062745), (0.047059, 0.568627, 0.062745), (0.043137, 0.552941, 0.058824),
           (0.043137, 0.533333, 0.058824), (0.043137, 0.517647, 0.054902), (0.039216, 0.501961, 0.054902),
           (0.039216, 0.486275, 0.05098), (0.039216, 0.466667, 0.05098), (0.035294, 0.45098, 0.047059), 
           (0.035294, 0.435294, 0.047059), (0.035294, 0.419608, 0.043137), (0.031373, 0.4, 0.043137),
           (0.031373, 0.384314, 0.039216), (0.035294, 0.368627, 0.035294), (0.113725, 0.407843, 0.035294), 
           (0.196078, 0.45098, 0.031373), (0.27451, 0.490196, 0.031373), (0.356863, 0.533333, 0.027451), 
           (0.435294, 0.572549, 0.027451), (0.517647, 0.615686, 0.023529), (0.596078, 0.658824, 0.023529),
           (0.678431, 0.698039, 0.019608), (0.756863, 0.741176, 0.019608), (0.839216, 0.780392, 0.015686),
           (0.917647, 0.823529, 0.015686), (1.0, 0.886275, 0.0), (1.0, 0.847059, 0.0), (1.0, 0.827451, 0.0), 
           (1.0, 0.788235, 0.0), (1.0, 0.768627, 0.0), (1.0, 0.733333, 0.0), (1.0, 0.713725, 0.0), 
           (1.0, 0.693725, 0.0), (1.0, 0.67451, 0.0), (1.0, 0.654902, 0.0), (1.0, 0.619608, 0.0), 
           (1.0, 0.6, 0.0), (1.0, 0.580392, 0.0), (1.0, 0.541176, 0.0), (1.0, 0.521569, 0.0), 
           (1.0, 0.501569, 0.0), (0.945098, 0.0, 0.0), 
           (0.917647, 0.0, 0.0), (0.890196, 0.0, 0.0), (0.862745, 0.0, 0.0), (0.835294, 0.0, 0.0), 
           (0.803922, 0.0, 0.0), (0.776471, 0.0, 0.0), (0.74902, 0.0, 0.0), (0.721569, 0.0, 0.0), 
           (0.694118, 0.0, 0.0), (0.666667, 0.0, 0.0), (0.639216, 0.0, 0.0), (0.607843, 0.0, 0.0),
           (0.580392, 0.0, 0.0), (0.552941, 0.0, 0.0), (0.52549, 0.0, 0.0), (0.498039, 0.0, 0.0), 
           (0.470588, 0.0, 0.0), (0.443137, 0.0, 0.0), (1.0, 0.960784, 1.0), 
           (1.0, 0.917647, 1.0), (1.0, 0.87451, 1.0), (1.0, 0.831373, 1.0), (1.0, 0.788235, 1.0), 
           (1.0, 0.745098, 1.0), (1.0, 0.701961, 1.0), (1.0, 0.658824, 1.0), (1.0, 0.615686, 1.0), 
           (1.0, 0.572549, 1.0), (1.0, 0.458824, 1.0), (0.988235, 0.419608, 0.992157), 
           (0.976471, 0.376471, 0.980392), (0.964706, 0.337255, 0.968627), (0.952941, 0.294118, 0.956863), 
           (0.941176, 0.25098, 0.945098), (0.929412, 0.211765, 0.937255), (0.917647, 0.168627, 0.92549), 
           (0.905882, 0.12549, 0.913725), (0.894118, 0.086275, 0.901961), (0.882353, 0.043137, 0.890196), 
           (0.698039, 0.0, 1.0), (0.67451, 0.0, 0.988235), (0.643137, 0.0, 0.968627), (0.607843, 0.0, 0.956863),
           (0.576471, 0.0, 0.937255), (0.533333, 0.0, 0.917647), (0.513725, 0.0, 0.909804),
           (0.47451, 0.0, 0.886275), (0.447059, 0.0, 0.866667), (0.411765, 0.0, 0.858824), 
           (0.388235, 0.0, 0.839216)]

colors3 = [(1,1,1), (0.961,0.949,0.847),
          (0.886,0.933,0.776),
          (0.776,0.910,0.737),
           (0.643,0.878,0.718),
          (0.494,0.835,0.722),
          (0.341,0.784,0.737),
          (0.204,0.722,0.753),
          (0.180,0.647,0.761),
          (0.278,0.557,0.757),
          (0.392,0.455,0.725),
          (0.478,0.333,0.671),
          (0.518,0.208,0.565),
          (0.502,0.078,0.431)]

cmap1 = ListedColormap(colors)
newcmap1 = ListedColormap(cmap1(np.linspace(0, 1, 16)))


cmap2 = ListedColormap(colors2)
newcmap2 = ListedColormap(cmap2(np.linspace(0, 0.9, 29)))

In [7]:
# Create the figure and plot background on different axes
for i in range(1,49):
    
    timestep=timeinit+timedelta(hours=i)
    crs = ccrs.Mercator()
    
    fig, axarr = plt.subplots(nrows=3, ncols=7, figsize=(25, 10), constrained_layout=False,
                              subplot_kw={'projection': crs})

    axlist = axarr.flatten()
    for ax in axlist:
        plot_background(ax)
        
    time2 = data_det_lpi['LPI_MAX'].metpy.time
    #clevs_dbz = np.arange(-2.5,72.5,2.5)
    clevs_lpi = np.arange(0,425,25)
    #clevs_gust = np.arange(50,210,20)
    # cmap = plt.get_cmap('gist_ncar')
    # newcmap = ListedColormap(cmap(np.linspace(0.15, 0.9, 30)))
    
    cf1 = axlist[20].contourf(data_det_lpi.longitude, data_det_lpi.latitude, det_lpi.metpy.loc[{'time': time2[i-1]}]*3.6, 
                          clevs_lpi, cmap=newcmap1, extend='max', transform=ccrs.PlateCarree())
    #ccf1= axlist[j].contour(data_rr.longitude, data_rr.latitude, rr.metpy.loc[{'step': time[i], 'number': member[j]}]-rr.metpy.loc[{'step': time[i-1], 'number': member[j]}],
                     #[15,25,35], colors='black', transform=ccrs.PlateCarree())
    #axlist[j].clabel(ccf1, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    axlist[20].set_title('Deterministic', fontsize=16)

    for j in range(0,20):
    
        # Upper left plot
        cf1 = axlist[j].contourf(data_lpi.longitude, data_lpi.latitude, lpi.metpy.loc[{'step': time[i], 'number': member[j]}]*3.6, 
                          clevs_lpi, cmap=newcmap1, extend='max', transform=ccrs.PlateCarree())
        #ccf1= axlist[0].contour(gust.longitude, gust.latitude, gust.metpy.loc[{'time': time[i]}]*3.6,
                         #clevs_gust, colors='darkviolet', transform=ccrs.PlateCarree())
        #axlist[0].clabel(ccf1, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
        axlist[j].set_title('Member '+str(j+1), fontsize=16)
        #cb1= fig.colorbar(cf1, ax=axlist[j], orientation='vertical',
                                  #shrink=1, fraction=0.03, pad=0)
        #cb1.set_label('dBZ', size='x-large')



    # Set height padding for plots
    fig.set_constrained_layout_pads(w_pad=0., h_pad=10, hspace=0., wspace=0.)
    cb = fig.colorbar(cf1, ax=axarr.ravel().tolist(), orientation='vertical', 
                      ticks=(0,25,50,75,100,125,150,175,200,225,250,275,300,325,350,375), fraction=0.03, aspect=30, pad=0.02)
    cb.set_label('J/kg', size='x-large')
    # Set figure title
    plt.gcf().text(0.135, 0.98, 'Model: ICON-D2-EPS 0.02° | ' + timeinit.strftime('Init: %d.%m.%Y %H:%M UTC | ')+timestep.strftime('Valid: %d.%m.%Y %H:%M UTC'), fontsize=20)
    plt.gcf().text(0.135, 0.94, 'Parameter: 1-hourly Maximum Lightning Potential Index', fontsize=20)
    #plt.gcf().text(0.6, 0.94, timeinit.strftime('Init: %d.%m.%Y %H:%M UTC / ')+timestep.strftime('Valid: %d.%m.%Y %H:%M UTC'), fontsize=20)
    #plt.gcf().text(0.55, 0.09, 'Note: Updraft helicity is vertically averaged between 500 and 6000 m AGL.', fontsize=10)

    # Display the plot
    time2 = str(i*1)
    base_filename='icond2eps_lpimax_'
    suffix='.jpeg'
    latest='latest'
    my_file = base_filename+time2+suffix
    print(my_file)
    plt.savefig(my_file, format="jpeg", bbox_inches='tight', dpi=100)
    plt.close(fig)

icond2eps_lpimax_1.jpeg


/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,


icond2eps_lpimax_2.jpeg


/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,


icond2eps_lpimax_3.jpeg


...

/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,


icond2eps_lpimax_47.jpeg


/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,


icond2eps_lpimax_48.jpeg


/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,


In [8]:
# Create the figure and plot background on different axes
for i in range(1,49):
    
    timestep=timeinit+timedelta(hours=i)
    crs = ccrs.Mercator()
    
    fig, axarr = plt.subplots(nrows=3, ncols=7, figsize=(25, 10), constrained_layout=False,
                              subplot_kw={'projection': crs})

    axlist = axarr.flatten()
    for ax in axlist:
        plot_background(ax)
        
    time2 = data_det_cape['CAPE_ML'].metpy.time
    #clevs_dbz = np.arange(-2.5,72.5,2.5)
    #clevs_uh = np.arange(0,650,50)
    clevs_cape = np.arange(100,3300,200)
    cmap = plt.get_cmap('gist_ncar')
    newcmap = ListedColormap(cmap(np.linspace(0.15, 0.95, 15)))
    
    cf1 = axlist[20].contourf(data_det_cape.longitude, data_det_cape.latitude, det_cape.metpy.loc[{'time': time2[i-1]}], 
                          clevs_cape, cmap=newcmap, transform=ccrs.PlateCarree())
    #ccf1= axlist[20].contour(data_det_cape.longitude, data_det_cape.latitude, det_cape.metpy.loc[{'time': time2[i-1]}],
                     #[10,30,50,70,90,110,130,150], colors='black', linestyles='dotted', linewidths=1, transform=ccrs.PlateCarree())
    #axlist[20].clabel(ccf1,fontsize=8, inline=1, inline_spacing=3, fmt='%i',  rightside_up=True)
    axlist[20].set_title('Deterministic', fontsize=16)

    for j in range(0,20):
    
        # Upper left plot
        cf1 = axlist[j].contourf(data_cape.longitude, data_cape.latitude, cape.metpy.loc[{'step': time[i], 'number': member[j]}], 
                          clevs_cape, cmap=newcmap, transform=ccrs.PlateCarree())
        #ccf1= axlist[j].contour(data_gust.longitude, data_gust.latitude, vmax.metpy.loc[{'step': time[i], 'number': member[j]}],
                         #[10,30,50,70,90,110,130,150],  colors='black', linestyles='dotted', linewidths=1, transform=ccrs.PlateCarree())
        #axlist[j].clabel(ccf1,fontsize=8, inline=1, inline_spacing=3, fmt='%i',  rightside_up=True)
        axlist[j].set_title('Member '+str(j+1), fontsize=16)
        #cb1= fig.colorbar(cf1, ax=axlist[j], orientation='vertical',
                                  #shrink=1, fraction=0.03, pad=0)
        #cb1.set_label('dBZ', size='x-large')



    # Set height padding for plots
    fig.set_constrained_layout_pads(w_pad=0., h_pad=10, hspace=0., wspace=0.)
    cb = fig.colorbar(cf1, ax=axarr.ravel().tolist(), orientation='vertical',
                       ticks=(100,300,500,700,900,1100,1300,1500,1700,1900,2100,2300,2500,2700,2900,3100,3300,3500),
                      fraction=0.03, aspect=30, pad=0.02)
    cb.set_label('J/kg', size='x-large')
    # Set figure title
    plt.gcf().text(0.135, 0.98, 'Model: ICON-D2-EPS 0.02° | ' + timeinit.strftime('Init: %d.%m.%Y %H:%M UTC | ')+timestep.strftime('Valid: %d.%m.%Y %H:%M UTC'), fontsize=20)
    plt.gcf().text(0.135, 0.94, 'Parameter: Mixed-Layer CAPE', fontsize=20)
    #plt.gcf().text(0.6, 0.94, timeinit.strftime('Init: %d.%m.%Y %H:%M UTC / ')+timestep.strftime('Valid: %d.%m.%Y %H:%M UTC'), fontsize=20)
    #plt.gcf().text(0.55, 0.09, 'Note: Updraft helicity is vertically averaged between 500 and 6000 m AGL.', fontsize=10)

    # Display the plot
    time2 = str(i*1)
    base_filename='icond2eps_cape_'
    suffix='.jpeg'
    latest='latest'
    my_file = base_filename+time2+suffix
    print(my_file)
    plt.savefig(my_file, format="jpeg", bbox_inches='tight', dpi=100)
    plt.close(fig)

icond2eps_cape_1.jpeg


/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,


icond2eps_cape_2.jpeg


/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,


icond2eps_cape_3.jpeg


...

/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,


icond2eps_cape_47.jpeg


/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,


icond2eps_cape_48.jpeg


/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,


In [9]:
# Create the figure and plot background on different axes

for i in range(1,49):
    
    timestep=timeinit+timedelta(hours=i)
    crs = ccrs.Mercator()
    
    fig, axarr = plt.subplots(nrows=3, ncols=7, figsize=(25, 10), constrained_layout=False,
                              subplot_kw={'projection': crs})

    axlist = axarr.flatten()
    for ax in axlist:
        plot_background(ax)
        
    time2 = data_det_cin['CIN_ML'].metpy.time
    #clevs_dbz = np.arange(-2.5,72.5,2.5)
    #clevs_uh = np.arange(0,650,50)
    clevs_cin = np.arange(10,270,20)
    #cmap = plt.get_cmap('gist_ncar')
    #newcmap = ListedColormap(cmap(np.linspace(0.15, 0.9, 17)))
    
    cf1 = axlist[20].contourf(data_det_cin.longitude, data_det_cin.latitude, det_cin.metpy.loc[{'time': time2[i-1]}], 
                          clevs_cin, cmap='Reds', extend='max', transform=ccrs.PlateCarree())
    #ccf1= axlist[20].contour(data_det_cin.longitude, data_det_cin.latitude, det_cin.metpy.loc[{'time': time2[i-1]}],
                     #[50,100], colors='black', linestyles='dotted', linewidths=1, transform=ccrs.PlateCarree())
    #axlist[20].clabel(ccf1,fontsize=8, inline=1, inline_spacing=3, fmt='%i',  rightside_up=True)
    axlist[20].set_title('Deterministic', fontsize=16)

    for j in range(0,20):
    
        # Upper left plot
        cf1 = axlist[j].contourf(data_cin.longitude, data_cin.latitude, cin.metpy.loc[{'step': time[i], 'number': member[j]}], 
                          clevs_cin, cmap='Reds', extend='max', transform=ccrs.PlateCarree())
        #ccf1= axlist[j].contour(data_cin.longitude, data_cin.latitude, cin.metpy.loc[{'step': time[i], 'number': member[j]}],
                         #[50,100],  colors='black', linestyles='dotted', linewidths=1, transform=ccrs.PlateCarree())
        #axlist[j].clabel(ccf1,fontsize=8, inline=1, inline_spacing=3, fmt='%i',  rightside_up=True)
        axlist[j].set_title('Member '+str(j+1), fontsize=16)
        #cb1= fig.colorbar(cf1, ax=axlist[j], orientation='vertical',
                                  #shrink=1, fraction=0.03, pad=0)
        #cb1.set_label('dBZ', size='x-large')



    # Set height padding for plots
    fig.set_constrained_layout_pads(w_pad=0., h_pad=10, hspace=0., wspace=0.)
    cb = fig.colorbar(cf1, ax=axarr.ravel().tolist(), orientation='vertical',
                    fraction=0.03, aspect=30, pad=0.02)
    cb.set_label('J/kg', size='x-large')
    # Set figure title
    plt.gcf().text(0.135, 0.98, 'Model: ICON-D2-EPS 0.02° | ' + timeinit.strftime('Init: %d.%m.%Y %H:%M UTC | ')+timestep.strftime('Valid: %d.%m.%Y %H:%M UTC'), fontsize=20)
    plt.gcf().text(0.135, 0.94, 'Parameter: Mixed-Layer CIN', fontsize=20)
    #plt.gcf().text(0.6, 0.94, timeinit.strftime('Init: %d.%m.%Y %H:%M UTC / ')+timestep.strftime('Valid: %d.%m.%Y %H:%M UTC'), fontsize=20)
    #plt.gcf().text(0.55, 0.09, 'Note: Updraft helicity is vertically averaged between 500 and 6000 m AGL.', fontsize=10)

    # Display the plot
    time2 = str(i*1)
    base_filename='icond2eps_cin_'
    suffix='.jpeg'
    latest='latest'
    my_file = base_filename+time2+suffix
    print(my_file)
    plt.savefig(my_file, format="jpeg", bbox_inches='tight', dpi=100)
    plt.close(fig)

icond2eps_cin_1.jpeg


/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,


icond2eps_cin_2.jpeg


/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,


icond2eps_cin_3.jpeg


...

/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,


icond2eps_cin_47.jpeg


/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,


icond2eps_cin_48.jpeg


/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,
